In [7]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [8]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [9]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [10]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [11]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [12]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[3:4]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2013-2014', 'value': '2013-2014 '}]
--Scrapping data for Year:  2013-2014
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BAKSA
--------Scrapping data for Block:  Barama
--------Scrapping data for Block:  Dhamdhama
--------Scrapping data for Block:  Gobardhana(BTC)
--------Scrapping data for Block:  Jalah(BTC)
--------Scrapping data for Block:  Nagrijuli
--------Scrapping data for Block:  Tamulpur
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  BAJALI
--------Scrapping data for Block:  BARPETA
--------Scrapping data for Block:  BHAWANIPUR
--------Scrapping data for Block:  CHAKCHAKA
--------S

--------Scrapping data for Block:  Barhampur
--------Scrapping data for Block:  Batadraba
--------Scrapping data for Block:  Binakandi
--------Scrapping data for Block:  Dhalpukhuri
--------Scrapping data for Block:  Dolongghat
--------Scrapping data for Block:  Jugijan
--------Scrapping data for Block:  Juria
--------Scrapping data for Block:  Kaliabor
--------Scrapping data for Block:  Kathiatoli
--------Scrapping data for Block:  Khagorijan
--------Scrapping data for Block:  Lowkhowa
--------Scrapping data for Block:  Lumding
--------Scrapping data for Block:  Odali
--------Scrapping data for Block:  Pachim Kaliabor
--------Scrapping data for Block:  Pakhimoria
--------Scrapping data for Block:  Raha
--------Scrapping data for Block:  Rupahihut
------Scrapping data for District:  NALBARI
--------Scrapping data for Block:  BARIGOG BANBHAG
--------Scrapping data for Block:  BARKHETRI
--------Scrapping data for Block:  BORBHAG
--------Scrapping data for Block:  MADHUPUR
--------Scrappi

--------Scrapping data for Block:  DARBHANGA
--------Scrapping data for Block:  GAURABAURAM
--------Scrapping data for Block:  GHANSHYAMPUR
--------Scrapping data for Block:  HANUMAN NAGAR
--------Scrapping data for Block:  HAYAGHAT
--------Scrapping data for Block:  JALE
--------Scrapping data for Block:  KEOTIRUNWAY
--------Scrapping data for Block:  KIRATPUR
--------Scrapping data for Block:  KUSHESHWAR ASTHAN
--------Scrapping data for Block:  KUSHESWAR ASTHAN EAST
--------Scrapping data for Block:  MANIGACHHI
--------Scrapping data for Block:  SINGHWARA
--------Scrapping data for Block:  TARDIH
------Scrapping data for District:  GAYA
--------Scrapping data for Block:  AMAS
--------Scrapping data for Block:  ATRI
--------Scrapping data for Block:  BANKEY BAZAR
--------Scrapping data for Block:  BARACHATTI
--------Scrapping data for Block:  BATHANI
--------Scrapping data for Block:  BELAGANJ
--------Scrapping data for Block:  BODHGAYA
--------Scrapping data for Block:  DOBHI
------

--------Scrapping data for Block:  Sakra
--------Scrapping data for Block:  SARAIYA
------Scrapping data for District:  NALANDA
--------Scrapping data for Block:  ASTHAWAN BLOCK
--------Scrapping data for Block:  BEN
--------Scrapping data for Block:  BIHARSARIF
--------Scrapping data for Block:  BIND BLOCK
--------Scrapping data for Block:  CHANDI BLOCK
--------Scrapping data for Block:  EKANGARSARAI
--------Scrapping data for Block:  GIRIYAK
--------Scrapping data for Block:  HARNAUT BLOCK
--------Scrapping data for Block:  HILSA
--------Scrapping data for Block:  ISLAMPUR BLOCK
--------Scrapping data for Block:  KARAIPARSURAI
--------Scrapping data for Block:  KATRISARAI
--------Scrapping data for Block:  NAGARNAUSA
--------Scrapping data for Block:  NOORSARAI
--------Scrapping data for Block:  PARWALPUR
--------Scrapping data for Block:  RAHUI BLOCK
--------Scrapping data for Block:  RAJGIR BLOCK
--------Scrapping data for Block:  SARMERA BLOCK
--------Scrapping data for Block:  SI

--------Scrapping data for Block:  ISUAPUR
--------Scrapping data for Block:  JALALPUR
--------Scrapping data for Block:  LAHLADPUR
--------Scrapping data for Block:  MAKER
--------Scrapping data for Block:  MANJHI
--------Scrapping data for Block:  MARHAURA
--------Scrapping data for Block:  MASHRAKH
--------Scrapping data for Block:  NAGRA
--------Scrapping data for Block:  PANAPUR
--------Scrapping data for Block:  PARSA
--------Scrapping data for Block:  REVELGANJ
--------Scrapping data for Block:  SONEPUR
--------Scrapping data for Block:  TARAIYA
------Scrapping data for District:  Sheikhpura
--------Scrapping data for Block:  ARIARI
--------Scrapping data for Block:  BARBHIGA
--------Scrapping data for Block:  CHEWARA
--------Scrapping data for Block:  GHAT KHUSUMBAHA
--------Scrapping data for Block:  SHEIKHPURA
--------Scrapping data for Block:  SHEOKHOPUR SARAI
------Scrapping data for District:  SHEOHAR
--------Scrapping data for Block:  Dumrikatsari
--------Scrapping data f

...

--------Scrapping data for Block:  Velairpad
--------Scrapping data for Block:  Vemsoor
--------Scrapping data for Block:  Venkatapuram
--------Scrapping data for Block:  Wazeed
--------Scrapping data for Block:  Wyra
--------Scrapping data for Block:  Yellandu
--------Scrapping data for Block:  Yerrupalem
------Scrapping data for District:  KRISHNA
--------Scrapping data for Block:  A Konduru
--------Scrapping data for Block:  Agiripalle
--------Scrapping data for Block:  Avanigadda
--------Scrapping data for Block:  Bantumilli
--------Scrapping data for Block:  Bapulapadu
--------Scrapping data for Block:  Challapalli
--------Scrapping data for Block:  Chandarlapadu
--------Scrapping data for Block:  Chatrai
--------Scrapping data for Block:  G Konduru
--------Scrapping data for Block:  Gampalagudem
--------Scrapping data for Block:  Gannavaram
--------Scrapping data for Block:  Ghantasala
--------Scrapping data for Block:  Gudivada
--------Scrapping data for Block:  Gudlavalleru
---

--------Scrapping data for Block:  GAJWEL
--------Scrapping data for Block:  HATHNOORA
--------Scrapping data for Block:  JAGDEVPUR
--------Scrapping data for Block:  JHARASANGAM
--------Scrapping data for Block:  JINNARAM
--------Scrapping data for Block:  KALHER
--------Scrapping data for Block:  KANGTI
--------Scrapping data for Block:  KOHIR
--------Scrapping data for Block:  KONDAPAK
--------Scrapping data for Block:  KONDAPUR
--------Scrapping data for Block:  KOWDIPALLI
--------Scrapping data for Block:  KULCHARAM
--------Scrapping data for Block:  MANOOR
--------Scrapping data for Block:  MEDAK
--------Scrapping data for Block:  MIRDODDI
--------Scrapping data for Block:  MULUGU
--------Scrapping data for Block:  MUNIPALLI
--------Scrapping data for Block:  NANGNUR
--------Scrapping data for Block:  NARAYANKHED
--------Scrapping data for Block:  NARSAPUR
--------Scrapping data for Block:  NYALKAL
--------Scrapping data for Block:  PAPANNAPET
--------Scrapping data for Block:  P

--------Scrapping data for Block:  Yeda Palle
--------Scrapping data for Block:  Yellareddy
------Scrapping data for District:  PRAKASAM
--------Scrapping data for Block:  Addanki
--------Scrapping data for Block:  Ardhaveedu
--------Scrapping data for Block:  Ballikuruva
--------Scrapping data for Block:  Bestavaripeta
--------Scrapping data for Block:  Chadrasekarapuram
--------Scrapping data for Block:  Chimakurthi
--------Scrapping data for Block:  Chinaganjam
--------Scrapping data for Block:  Chirala
--------Scrapping data for Block:  Cumbum
--------Scrapping data for Block:  Darsi
--------Scrapping data for Block:  Donakonda
--------Scrapping data for Block:  Dornala
--------Scrapping data for Block:  Giddaluru
--------Scrapping data for Block:  Gudluru
--------Scrapping data for Block:  Hanumanthunipadu
--------Scrapping data for Block:  Inkollu
--------Scrapping data for Block:  Janakavarampanguluru
--------Scrapping data for Block:  Kandukur
--------Scrapping data for Block: 

--------Scrapping data for Block:  Dattirajeru
--------Scrapping data for Block:  Denkada
--------Scrapping data for Block:  Gajapathinagaram
--------Scrapping data for Block:  Gantyada
--------Scrapping data for Block:  Garividi
--------Scrapping data for Block:  Garugubilli
--------Scrapping data for Block:  Gummalakshmipuram
--------Scrapping data for Block:  Gurla
--------Scrapping data for Block:  Jami
--------Scrapping data for Block:  Jiyyamma Valasa
--------Scrapping data for Block:  Komarada
--------Scrapping data for Block:  Kothavalasa
--------Scrapping data for Block:  Kurupam
--------Scrapping data for Block:  Lakkavarapukota
--------Scrapping data for Block:  Makkuva
--------Scrapping data for Block:  Mentada
--------Scrapping data for Block:  Merakamudidam
--------Scrapping data for Block:  Nellimarla
--------Scrapping data for Block:  Pachipenta
--------Scrapping data for Block:  Parvathipuram
--------Scrapping data for Block:  Pusapatirega
--------Scrapping data for Bl

--------Scrapping data for Block:  Challakere
--------Scrapping data for Block:  Chitradurga
--------Scrapping data for Block:  Hiriyur
--------Scrapping data for Block:  Holalkere
--------Scrapping data for Block:  Hosadurga
--------Scrapping data for Block:  Molakalmuru
------Scrapping data for District:  DakshinaKannada
--------Scrapping data for Block:  Bantwal
--------Scrapping data for Block:  Belthangadi
--------Scrapping data for Block:  Mangaluru
--------Scrapping data for Block:  Puttur
--------Scrapping data for Block:  Sullia
------Scrapping data for District:  Davanagere
--------Scrapping data for Block:  Channagiri
--------Scrapping data for Block:  Davanagere
--------Scrapping data for Block:  Harappanahalli
--------Scrapping data for Block:  Harihara
--------Scrapping data for Block:  Honnali
--------Scrapping data for Block:  Jagalur
------Scrapping data for District:  Dharwad
--------Scrapping data for Block:  Dharwad
--------Scrapping data for Block:  Hubballi
------